https://ipip.ori.org/New_IPIP-50-item-scale.htm

# gradio

In [1]:
#os.system('pip install openpyxl') #works for huggingface-spaces
#score of each latent variable ranges in [10, 50]
def correct_score(score, big_5_indicator):
    big_5_sign = big_5_indicator[0]
    big_5_num = int(big_5_indicator[1])
    dict1 = {
        1 : 'Extraversion',
        2 : 'Agreeableness',
        3 : 'Conscientiousness',
        4 : 'Neuroticism',
        5 : 'Openness'
    }
    if big_5_sign=='+':
        return [dict1[big_5_num], score]
    elif big_5_sign =='-':
        return [dict1[big_5_num], 6-score]
# correct_score(3, big_5_indicator='-2')

def make_question(q):
    q = gr.Radio(choices=[1, 2, 3, 4, 5], label=q, value=1) #, value=5
    return q

def calculate_personality_score(questions, list_questions):
    personality = {
        'Extraversion': 0,
        'Agreeableness': 0,
        'Conscientiousness': 0,
        'Neuroticism': 0,
        'Openness': 0
    }
    for question in list_questions:
        big_5_indicator = questions[question[0]]
        score = correct_score(question[1], big_5_indicator=big_5_indicator)
        personality[score[0]] += score[1]
    return personality

In [3]:
import gradio as gr
import pandas as pd
import numpy as np
import os

#
df_big5_test = pd.read_csv('Big5.csv', sep=';', header=None)
df_big5_test = df_big5_test[[0, 6]]
df_big5_test.columns = ['question', 'score']
df_big5_test['score'] = df_big5_test['score'].apply(lambda x : x.replace('(', '').replace(')', '')[::-1])
# df.index = df.pop('question')
questions = dict()
for el in df_big5_test.values.tolist():
    questions[el[0]] = el[1]
questions

#the first module becomes text1, the second module file1
def greet(*args): 
    args_list = [item for item in args]

    #extract big5
    q_list = list(questions)
    a_list = args_list[:]
    list_total = [[q_list[x], a_list[x]] for x in range(len(a_list))]
    personality = calculate_personality_score(questions, list_total)
    personality = { x : personality[x]/50 for x in personality}
    # personality = [personality['Openness'], personality['Conscientiousness'], personality['Extraversion'], personality['Agreeableness'], personality['Neuroticism']]
    # personality = [x/50 for x in personality]

    #to return a file:
    #return 'new.xlsx'
    return personality

iface = gr.Interface(
    fn=greet, 
    inputs=[make_question(q) for q in list(questions)], 
        outputs=["text"]
    )
iface.launch(share=False)

Running on local URL:  http://127.0.0.1:7862

To create a public link, set `share=True` in `launch()`.


(<gradio.routes.App at 0x27427d923a0>, 'http://127.0.0.1:7862/', None)